# 3. Building Compositional Space Complexes to Express Elaborate Design Problems

--> ***(before running this code, please consult Quick Start to make sure everything is set up)***

--> You will need the same dependencies as in [Tutorial No.2](02.AdditiveManufacturingPathPlanning.ipynb) (i.e., `pycalphad` and `pathfinding`), and additionally `igraph` in order to efficiently visualize the examples presented in this tutorial. If you are running this in Codespaces, everything has been pre-installed for you.

**In this tutorial, we will build upon `nimplex`'s graph representations and leverage our ability to combine them together without affecting the way we express the problem at hand 


demonstrate how effortless it is to dramatically speed up the exploration of feasible compositional spaces in high dimensional spaces through employing `nimplex`'s graph representations that abstract the underlying problem and dimensionality.**

In [167]:
import nimplex
from utils import stitching
from utils import plotting

In [168]:
import igraph as ig
import plotly.graph_objs as go
import numpy as np
import random

In [169]:
dim = 4
ndiv = 6
gridAtt, nList = nimplex.simplex_graph_py(dim, ndiv)

In [170]:
edges = []
for i in range(len(gridAtt)):
    for n in nList[i]:
        edges.append((i,n))

In [171]:
def plotGraph(edges: list):
    # Lets generate some seed positions for the nodes
    G = ig.Graph(edges)
    layout = G.layout_kamada_kawai(dim=3)
    layout_array = np.array(layout.coords)
    # Create edge traces
    edge_traces = []
    for edge in G.es:
        start, end = edge.tuple
        x0, y0, z0 = layout_array[start]
        x1, y1, z1 = layout_array[end]
        width = 5
        edge_trace = go.Scatter3d(x=[x0, x1], y=[y0, y1], z=[z0, z1],
                                line=dict(width=width, color='lightgray'),
                                opacity=0.2,
                                hoverinfo='none', mode='lines')
        edge_traces.append(edge_trace)

    node_trace = go.Scatter3d(x=layout_array[:, 0], y=layout_array[:, 1], z=layout_array[:, 2],
                            mode='markers',
                            marker=dict(size=3, 
                                        opacity=0.5,
                                        line=None,
                                        color='blue'),
                            
                            text=[f"Node {i}" for i in range(len(gridAtt))],
                            hoverinfo='text')

    # Create figure
    fig = go.Figure(data=edge_traces + [node_trace])

    # Update layout
    fig.update_layout(
        title='3D Graph with Feasibility Types',
        scene=dict(
            xaxis=dict(visible=False),
            yaxis=dict(visible=False),
            zaxis=dict(visible=False),
        ),
        showlegend=False,
        margin=dict(l=0, r=0, b=0, t=0),
        width=800
    )

    fig.show()

In [172]:
plotGraph(edges)

In [173]:
sys1 = ["A", "B", "C", "D"]
sys2 = ["B", "C", "D", "E"]
sys3 = ["B", "D", "E", "F"]

In [174]:
offset = len(gridAtt)
for i in range(len(gridAtt)):
    for n in nList[i]:
        edges.append((i+offset,n+offset))
for i in range(len(gridAtt)):
    for n in nList[i]:
        edges.append((i+offset*2,n+offset*2))

In [175]:
plotGraph(edges)

In [176]:
stitchingPoints = stitching.findStitchingPoints_py(dim, ndiv, components=["A", "B", "C", "D"])
print(stitchingPoints["A-B"])

[83, 82, 79, 73, 63, 48, 27]


In [177]:
stitchingPoints1 = stitching.findStitchingPoints_py(dim, ndiv, components=sys1, offset=0)
stitchingPoints2 = stitching.findStitchingPoints_py(dim, ndiv, components=sys2, offset=len(gridAtt))
stitchingPoints3 = stitching.findStitchingPoints_py(dim, ndiv, components=sys3, offset=len(gridAtt)*2)

In [178]:
for i, j in zip(stitchingPoints1["B-C-D"], stitchingPoints2["B-C-D"]):
    edges.append((i, j))

In [179]:
for i, j in zip(stitchingPoints2["B-D-E"], stitchingPoints3["B-D-E"]):
    edges.append((i, j))

In [180]:
plotGraph(edges)

In [181]:
from itertools import combinations
elements = ["A", "B", "C", "D"]
ternaries = list(combinations(elements, 3))
print(ternaries)

[('A', 'B', 'C'), ('A', 'B', 'D'), ('A', 'C', 'D'), ('B', 'C', 'D')]


In [182]:
gridAtt, nList = nimplex.simplex_graph_py(3,12)

In [183]:
edges = []
# Ternaries
for i, ternary in enumerate(ternaries):
    offset = i*len(gridAtt)
    for i in range(len(gridAtt)):
        for n in nList[i]:
            edges.append((i+offset,n+offset))

In [184]:
plotGraph(edges)

In [185]:
stitchingBinaries = {}

for i, combo1 in enumerate(ternaries):
    for j, combo2 in enumerate(ternaries[i+1:], start=i+1):
        common = set(combo1) & set(combo2)
        if len(common) == 2:
            overlap = tuple(sorted(common))
            if overlap not in stitchingBinaries:
                stitchingBinaries[overlap] = []
            stitchingBinaries[overlap].append((i, j))

for overlap, pairs in stitchingBinaries.items():
    print(f"{overlap}: occurs between ternary {pairs}")

('A', 'B'): occurs between ternary [(0, 1)]
('A', 'C'): occurs between ternary [(0, 2)]
('B', 'C'): occurs between ternary [(0, 3)]
('A', 'D'): occurs between ternary [(1, 2)]
('B', 'D'): occurs between ternary [(1, 3)]
('C', 'D'): occurs between ternary [(2, 3)]


In [186]:
for stitchingBinary, ternaryPair in stitchingBinaries.items():
    ternary1, ternary2 = ternaryPair[0][0], ternaryPair[0][1]
    stitching1 = stitching.findStitchingPoints_py(
        3, 12, 
        components=ternaries[ternary1],
        offset=ternary1*len(gridAtt)
        )["-".join(stitchingBinary)]
    stitching2 = stitching.findStitchingPoints_py(
        3, 12, 
        components=ternaries[ternary2],
        offset=ternary2*len(gridAtt)
        )["-".join(stitchingBinary)]
    print(f"Stitching {ternary1} and {ternary2} at {stitchingBinary} from {stitching1} to {stitching2}")
    for i, j in zip(stitching1, stitching2):
        edges.append((i, j))

Stitching 0 and 1 at ('A', 'B') from [90, 89, 87, 84, 80, 75, 69, 62, 54, 45, 35, 24, 12] to [181, 180, 178, 175, 171, 166, 160, 153, 145, 136, 126, 115, 103]
Stitching 0 and 2 at ('A', 'C') from [90, 88, 85, 81, 76, 70, 63, 55, 46, 36, 25, 13, 0] to [272, 271, 269, 266, 262, 257, 251, 244, 236, 227, 217, 206, 194]
Stitching 0 and 3 at ('B', 'C') from [12, 11, 10, 9, 8, 7, 6, 5, 4, 3, 2, 1, 0] to [363, 362, 360, 357, 353, 348, 342, 335, 327, 318, 308, 297, 285]
Stitching 1 and 2 at ('A', 'D') from [181, 179, 176, 172, 167, 161, 154, 146, 137, 127, 116, 104, 91] to [272, 270, 267, 263, 258, 252, 245, 237, 228, 218, 207, 195, 182]
Stitching 1 and 3 at ('B', 'D') from [103, 102, 101, 100, 99, 98, 97, 96, 95, 94, 93, 92, 91] to [363, 361, 358, 354, 349, 343, 336, 328, 319, 309, 298, 286, 273]
Stitching 2 and 3 at ('C', 'D') from [194, 193, 192, 191, 190, 189, 188, 187, 186, 185, 184, 183, 182] to [285, 284, 283, 282, 281, 280, 279, 278, 277, 276, 275, 274, 273]


In [187]:
plotGraph(edges)

In [188]:
from itertools import combinations
elements = ["A", "B", "C", "D", "E"]
ternaries = list(combinations(elements, 3))
print(ternaries)

[('A', 'B', 'C'), ('A', 'B', 'D'), ('A', 'B', 'E'), ('A', 'C', 'D'), ('A', 'C', 'E'), ('A', 'D', 'E'), ('B', 'C', 'D'), ('B', 'C', 'E'), ('B', 'D', 'E'), ('C', 'D', 'E')]


In [189]:
gridAtt, nList = nimplex.simplex_graph_py(3,12)

In [190]:
edges = []
# Ternaries
for i, ternary in enumerate(ternaries):
    offset = i*len(gridAtt)
    for i in range(len(gridAtt)):
        for n in nList[i]:
            edges.append((i+offset,n+offset))


In [191]:
plotGraph(edges)

In [192]:
stitchingBinaries = {}

for i, combo1 in enumerate(ternaries):
    for j, combo2 in enumerate(ternaries[i+1:], start=i+1):
        common = set(combo1) & set(combo2)
        if len(common) == 2:
            overlap = tuple(sorted(common))
            if overlap not in stitchingBinaries:
                stitchingBinaries[overlap] = []
            stitchingBinaries[overlap].append((i, j))

for overlap, pairs in stitchingBinaries.items():
    print(f"{overlap}: occurs between ternary {pairs}")

('A', 'B'): occurs between ternary [(0, 1), (0, 2), (1, 2)]
('A', 'C'): occurs between ternary [(0, 3), (0, 4), (3, 4)]
('B', 'C'): occurs between ternary [(0, 6), (0, 7), (6, 7)]
('A', 'D'): occurs between ternary [(1, 3), (1, 5), (3, 5)]
('B', 'D'): occurs between ternary [(1, 6), (1, 8), (6, 8)]
('A', 'E'): occurs between ternary [(2, 4), (2, 5), (4, 5)]
('B', 'E'): occurs between ternary [(2, 7), (2, 8), (7, 8)]
('C', 'D'): occurs between ternary [(3, 6), (3, 9), (6, 9)]
('C', 'E'): occurs between ternary [(4, 7), (4, 9), (7, 9)]
('D', 'E'): occurs between ternary [(5, 8), (5, 9), (8, 9)]


In [193]:
for stitchingBinary, ternaryPairList in stitchingBinaries.items():
    for ternaryPair in ternaryPairList:
        ternary1, ternary2 = ternaryPair[0], ternaryPair[1]
        stitching1 = stitching.findStitchingPoints_py(
            3, 12, 
            components=ternaries[ternary1],
            offset=ternary1*len(gridAtt)
            )["-".join(stitchingBinary)]
        stitching2 = stitching.findStitchingPoints_py(
            3, 12, 
            components=ternaries[ternary2],
            offset=ternary2*len(gridAtt)
            )["-".join(stitchingBinary)]
        print(f"Stitching {ternary1} and {ternary2} at {stitchingBinary} from {stitching1} to {stitching2}")
        for i, j in zip(stitching1, stitching2):
            edges.append((i, j))

Stitching 0 and 1 at ('A', 'B') from [90, 89, 87, 84, 80, 75, 69, 62, 54, 45, 35, 24, 12] to [181, 180, 178, 175, 171, 166, 160, 153, 145, 136, 126, 115, 103]
Stitching 0 and 2 at ('A', 'B') from [90, 89, 87, 84, 80, 75, 69, 62, 54, 45, 35, 24, 12] to [272, 271, 269, 266, 262, 257, 251, 244, 236, 227, 217, 206, 194]
Stitching 1 and 2 at ('A', 'B') from [181, 180, 178, 175, 171, 166, 160, 153, 145, 136, 126, 115, 103] to [272, 271, 269, 266, 262, 257, 251, 244, 236, 227, 217, 206, 194]
Stitching 0 and 3 at ('A', 'C') from [90, 88, 85, 81, 76, 70, 63, 55, 46, 36, 25, 13, 0] to [363, 362, 360, 357, 353, 348, 342, 335, 327, 318, 308, 297, 285]
Stitching 0 and 4 at ('A', 'C') from [90, 88, 85, 81, 76, 70, 63, 55, 46, 36, 25, 13, 0] to [454, 453, 451, 448, 444, 439, 433, 426, 418, 409, 399, 388, 376]
Stitching 3 and 4 at ('A', 'C') from [363, 362, 360, 357, 353, 348, 342, 335, 327, 318, 308, 297, 285] to [454, 453, 451, 448, 444, 439, 433, 426, 418, 409, 399, 388, 376]
Stitching 0 and 6 at (

In [194]:
plotGraph(edges)

In [274]:
elementalSpaceComponents = ["Ti", "Zr", "Hf", "W", "Nb", "Ta", "Mo"]
attainableSpaceComponents = ["Ti50Zr50", "Hf95Ti5", "NbTaWHf", "Mo80Nb10W10", "TiTa2", "Nb96Mo3W1", "Zr49 Hf1 Mo50"]
attainableSpaceComponentPositions = [
    #Ti, Zr, Hf,  W, Nb, Ta, Mo
    [50, 50,  0,  0,  0,  0,  0], 
    [ 5,  0, 95,  0,  0,  0,  0], 
    [ 0,  0, 25, 25, 25, 25,  0], 
    [ 0,  0,  0, 10, 10,  0, 80],
    [33,  0,  0,  0,  0, 66,  0],
    [ 0,  0,  0,  1, 96,  0,  3],
    [ 0, 49,  1,  0,  0,  0, 50]
]    
ternaries = list(combinations(attainableSpaceComponents, 3))
ternaries_CompPos = list(combinations(attainableSpaceComponentPositions, 3))
ndiv = 8
gridAtt, nList = nimplex.simplex_graph_py(3, ndiv)

for tern, terncp in zip(ternaries, ternaries_CompPos):
    print(f"{str(tern):<40} -> {terncp}")

('Ti50Zr50', 'Hf95Ti5', 'NbTaWHf')       -> ([50, 50, 0, 0, 0, 0, 0], [5, 0, 95, 0, 0, 0, 0], [0, 0, 25, 25, 25, 25, 0])
('Ti50Zr50', 'Hf95Ti5', 'Mo80Nb10W10')   -> ([50, 50, 0, 0, 0, 0, 0], [5, 0, 95, 0, 0, 0, 0], [0, 0, 0, 10, 10, 0, 80])
('Ti50Zr50', 'Hf95Ti5', 'TiTa2')         -> ([50, 50, 0, 0, 0, 0, 0], [5, 0, 95, 0, 0, 0, 0], [33, 0, 0, 0, 0, 66, 0])
('Ti50Zr50', 'Hf95Ti5', 'Nb96Mo3W1')     -> ([50, 50, 0, 0, 0, 0, 0], [5, 0, 95, 0, 0, 0, 0], [0, 0, 0, 1, 96, 0, 3])
('Ti50Zr50', 'Hf95Ti5', 'Zr49 Hf1 Mo50') -> ([50, 50, 0, 0, 0, 0, 0], [5, 0, 95, 0, 0, 0, 0], [0, 49, 1, 0, 0, 0, 50])
('Ti50Zr50', 'NbTaWHf', 'Mo80Nb10W10')   -> ([50, 50, 0, 0, 0, 0, 0], [0, 0, 25, 25, 25, 25, 0], [0, 0, 0, 10, 10, 0, 80])
('Ti50Zr50', 'NbTaWHf', 'TiTa2')         -> ([50, 50, 0, 0, 0, 0, 0], [0, 0, 25, 25, 25, 25, 0], [33, 0, 0, 0, 0, 66, 0])
('Ti50Zr50', 'NbTaWHf', 'Nb96Mo3W1')     -> ([50, 50, 0, 0, 0, 0, 0], [0, 0, 25, 25, 25, 25, 0], [0, 0, 0, 1, 96, 0, 3])
('Ti50Zr50', 'NbTaWHf', 'Zr49 Hf1 Mo5

In [275]:
nList[1]

[0, 2, 9, 10]

In [276]:
# Edges list for graph plotting and path finding purposes
edges = []
# Connectivity list within each subsystem
graphN = [[] for i in range(len(gridAtt * len(ternaries)))]
# Connectivity list between subsystems
graphNS = [[] for i in range(len(graphN))]
compositions = []
# Iterate over ternaries
for i, terncp in enumerate(ternaries_CompPos):
    offset = i*len(gridAtt)
    for j in range(len(gridAtt)):
        for n in nList[j]:
            edges.append((j+offset,n+offset))
            graphN[j+offset].append(n+offset)
    gridAttTemp, gridElTemp = nimplex.embeddedpair_simplex_grid_fractional_py(terncp, ndiv)
    compositions += gridElTemp

In [277]:
len(compositions)

1575

In [278]:
stitchingBinaries = {}

for i, combo1 in enumerate(ternaries):
    for j, combo2 in enumerate(ternaries[i+1:], start=i+1):
        common = set(combo1) & set(combo2)
        if len(common) == 2:
            overlap = tuple(sorted(common))
            if overlap not in stitchingBinaries:
                stitchingBinaries[overlap] = []
            stitchingBinaries[overlap].append((i, j))

for overlap, pairs in stitchingBinaries.items():
    print(f"{overlap}: occurs between ternary {pairs}")

('Hf95Ti5', 'Ti50Zr50'): occurs between ternary [(0, 1), (0, 2), (0, 3), (0, 4), (1, 2), (1, 3), (1, 4), (2, 3), (2, 4), (3, 4)]
('NbTaWHf', 'Ti50Zr50'): occurs between ternary [(0, 5), (0, 6), (0, 7), (0, 8), (5, 6), (5, 7), (5, 8), (6, 7), (6, 8), (7, 8)]
('Hf95Ti5', 'NbTaWHf'): occurs between ternary [(0, 15), (0, 16), (0, 17), (0, 18), (15, 16), (15, 17), (15, 18), (16, 17), (16, 18), (17, 18)]
('Mo80Nb10W10', 'Ti50Zr50'): occurs between ternary [(1, 5), (1, 9), (1, 10), (1, 11), (5, 9), (5, 10), (5, 11), (9, 10), (9, 11), (10, 11)]
('Hf95Ti5', 'Mo80Nb10W10'): occurs between ternary [(1, 15), (1, 19), (1, 20), (1, 21), (15, 19), (15, 20), (15, 21), (19, 20), (19, 21), (20, 21)]
('Ti50Zr50', 'TiTa2'): occurs between ternary [(2, 6), (2, 9), (2, 12), (2, 13), (6, 9), (6, 12), (6, 13), (9, 12), (9, 13), (12, 13)]
('Hf95Ti5', 'TiTa2'): occurs between ternary [(2, 16), (2, 19), (2, 22), (2, 23), (16, 19), (16, 22), (16, 23), (19, 22), (19, 23), (22, 23)]
('Nb96Mo3W1', 'Ti50Zr50'): occur

In [279]:
for stitchingBinary, ternaryPairList in stitchingBinaries.items():
    for ternaryPair in ternaryPairList:
        ternary1, ternary2 = ternaryPair[0], ternaryPair[1]
        stitching1 = stitching.findStitchingPoints_py(
            3, ndiv, 
            components=ternaries[ternary1],
            offset=ternary1*len(gridAtt)
            )["-".join(stitchingBinary)]
        stitching2 = stitching.findStitchingPoints_py(
            3, ndiv, 
            components=ternaries[ternary2],
            offset=ternary2*len(gridAtt)
            )["-".join(stitchingBinary)]
        print(f"Stitching {ternary1} and {ternary2} at {stitchingBinary} from {stitching1} to {stitching2}")
        for i, j in zip(stitching1, stitching2):
            edges.append((i, j))
            graphNS[i].append(j)

Stitching 0 and 1 at ('Hf95Ti5', 'Ti50Zr50') from [8, 16, 23, 29, 34, 38, 41, 43, 44] to [53, 61, 68, 74, 79, 83, 86, 88, 89]
Stitching 0 and 2 at ('Hf95Ti5', 'Ti50Zr50') from [8, 16, 23, 29, 34, 38, 41, 43, 44] to [98, 106, 113, 119, 124, 128, 131, 133, 134]
Stitching 0 and 3 at ('Hf95Ti5', 'Ti50Zr50') from [8, 16, 23, 29, 34, 38, 41, 43, 44] to [143, 151, 158, 164, 169, 173, 176, 178, 179]
Stitching 0 and 4 at ('Hf95Ti5', 'Ti50Zr50') from [8, 16, 23, 29, 34, 38, 41, 43, 44] to [188, 196, 203, 209, 214, 218, 221, 223, 224]
Stitching 1 and 2 at ('Hf95Ti5', 'Ti50Zr50') from [53, 61, 68, 74, 79, 83, 86, 88, 89] to [98, 106, 113, 119, 124, 128, 131, 133, 134]
Stitching 1 and 3 at ('Hf95Ti5', 'Ti50Zr50') from [53, 61, 68, 74, 79, 83, 86, 88, 89] to [143, 151, 158, 164, 169, 173, 176, 178, 179]
Stitching 1 and 4 at ('Hf95Ti5', 'Ti50Zr50') from [53, 61, 68, 74, 79, 83, 86, 88, 89] to [188, 196, 203, 209, 214, 218, 221, 223, 224]
Stitching 2 and 3 at ('Hf95Ti5', 'Ti50Zr50') from [98, 106, 113

In [280]:
len(edges)

9450

In [281]:
# Plot is quite interesting, being a much more complex version of the last one, but it has too many points for a small Codespace VM to display smootly. You can remove `#` and 
# plotGraph(edges)

In [282]:
from pycalphad import Database
dbf = Database("CrHfMoNbTaTiVWZr_9element_Feb2023.tdb")
phases = list(set(dbf.phases.keys()))
print(elementalSpaceComponents)
print(f'Loaded TDB file with phases considered: {phases}')

['Ti', 'Zr', 'Hf', 'W', 'Nb', 'Ta', 'Mo']
Loaded TDB file with phases considered: ['LIQUID', 'LAVES_C36', 'LAVES_C15', 'HCP_A3', 'LAVES_C14', 'BCC_A2', 'FCC_A1']


In [283]:
from myPycalphadCallable import equilibrium_callable

In [284]:
print(compositions[0])
equilibrium_callable(compositions[0])

[0.0, 0.0, 0.25, 0.25, 0.25, 0.25, 0.0]


['HCP_A3', 'BCC_A2']

In [285]:
startingNodes = [0, 1538] + random.sample(range(len(compositions)), 8)
print(f"Starting nodes: {startingNodes}")

for startingNode in startingNodes:
    print(f"Starting node: {compositions[startingNode]}")

Starting nodes: [0, 1538, 475, 827, 1523, 1240, 411, 769, 1561, 932]
Starting node: [0.0, 0.0, 0.25, 0.25, 0.25, 0.25, 0.0]
Starting node: [0.0, 0.0, 0.0, 0.01, 0.96, 0.0, 0.03]
Starting node: [0.1875, 0.1875, 0.0, 0.0175, 0.4925, 0.0, 0.115]
Starting node: [0.0125, 0.3675, 0.245, 0.0, 0.0, 0.0, 0.375]
Starting node: [0.0, 0.0, 0.0, 0.06625, 0.4225, 0.0, 0.51125]
Starting node: [0.0, 0.245, 0.09875, 0.10625, 0.10625, 0.09375, 0.35]
Starting node: [0.08333333333333333, 0.0, 0.0, 0.07500000000000001, 0.07500000000000001, 0.16666666666666666, 0.6000000000000001]
Starting node: [0.0, 0.0, 0.125, 0.13, 0.605, 0.125, 0.015]
Starting node: [0.16666666666666666, 0.18375, 0.00375, 0.00125, 0.12, 0.3333333333333333, 0.19125]
Starting node: [0.025, 0.0, 0.475, 0.0275, 0.265, 0.0, 0.20750000000000002]


In [286]:
from tqdm.contrib.concurrent import process_map

In [287]:
gridFeasible = [None]*len(compositions)
queue = startingNodes.copy()
explored = set()
calcCount = 0

In [290]:
while len(queue)>0:
    print(f"Queue: {queue}")
    # Calculate feasibilities of the current queue
    elPositions = [compositions[i] for i in queue]
    if len(queue)>3:
        phases = process_map(equilibrium_callable, elPositions, max_workers=4)
    else:
        phases = [equilibrium_callable(elP) for elP in elPositions]
    feasibilities = [len(set(p) & set(['LAVES_C15', 'LAVES_C36', 'LAVES_C14', 'LIQUID']))==0 and p!=[] for p in phases]

    calcCount += len(feasibilities)
    explored = explored.union(queue)

    # Create next queue based on neighbors of feasible points
    nextQueue = set()
    nextQueuePlusEquivalent = set()
    for f, i in zip(feasibilities, queue):
        # Explored point
        gridFeasible[i] = f

        # And equivalent explored points based on system stitching
        explored = explored.union(graphNS[i])
        for eq in graphNS[i]:
            gridFeasible[eq] = f

        # Expand to neighbors of the point and equivalent points (only if the node has been feasible)
        if f:
            # Node neighbors in the same subsystem
            for n in graphN[i]:
                if n not in explored and n not in nextQueuePlusEquivalent:
                    nextQueue.add(n)
                    nextQueuePlusEquivalent = nextQueuePlusEquivalent.union([n] + graphNS[n])
            # Equivalent nodes neighbors in other subsystems
            for eq in graphNS[i]:
                for n in graphN[eq]:
                    if n not in explored and n not in nextQueuePlusEquivalent:
                        nextQueue.add(n)
                        nextQueuePlusEquivalent = nextQueuePlusEquivalent.union([n] + graphNS[n])

    print(f"Calculations done: {calcCount:<5} | Explored points: {len(explored):<5}")
    queue = list(nextQueue)

Queue: [0, 1538, 475, 827, 1523, 1240, 411, 769, 1561, 932]


  0%|          | 0/10 [00:00<?, ?it/s]

Calculations done: 10    | Explored points: 28   
Queue: [768, 1, 1537, 770, 1285, 9, 1546, 777, 778, 1291, 1555, 1556, 277, 1432, 1560, 410, 1435, 412, 1562, 1565, 1566, 419, 420, 1195, 1201, 322, 1477, 1480, 1378, 869, 870, 1383, 232, 1518, 367, 1519, 1522, 1139, 1140, 1526]


  0%|          | 0/40 [00:00<?, ?it/s]

Calculations done: 50    | Explored points: 106  
Queue: [1536, 2, 1545, 10, 1548, 1549, 1550, 17, 1553, 1554, 1557, 1563, 1567, 1569, 1570, 1138, 1141, 1146, 1147, 1148, 1165, 1169, 1188, 1189, 682, 1196, 690, 1202, 1206, 1210, 727, 735, 231, 1255, 240, 1278, 1279, 767, 771, 772, 1286, 776, 779, 780, 1292, 1296, 784, 785, 786, 276, 1300, 285, 817, 825, 1345, 321, 330, 1371, 1372, 1377, 868, 1382, 871, 1387, 1390, 366, 1394, 375, 1427, 1428, 1431, 1433, 409, 1434, 1437, 1438, 413, 418, 421, 1473, 1482, 1513, 1514, 1525]


...

Calculations done: 942   | Explored points: 1231 
Queue: [640, 100, 137, 107, 145, 632, 92]


  0%|          | 0/7 [00:00<?, ?it/s]

Calculations done: 949   | Explored points: 1238 
Queue: [99, 136, 144, 152, 91]


  0%|          | 0/5 [00:00<?, ?it/s]

Calculations done: 954   | Explored points: 1243 
Queue: [159, 90, 135]
Calculations done: 957   | Explored points: 1246 


In [291]:
feasibleCount = 0
for f in gridFeasible:
    if f:
        feasibleCount += 1
print(f"Feasible points: {feasibleCount} out of {len(gridFeasible)}")

Feasible points: 1041 out of 1575


In [293]:
gridPhasesComplete = process_map(equilibrium_callable, compositions)

/var/folders/3k/vsgxtfbs1ns7mvh51w1x_6lh0000gn/T/ipykernel_25703/426994125.py:1: TqdmWarning:

Iterable length 1575 > 1000 but `chunksize` is not set. This may seriously degrade multiprocess performance. Set `chunksize=1` or more.



  0%|          | 0/1575 [00:00<?, ?it/s]

In [295]:
gridFeasibleComplete = [len(set(p) & set(['LAVES_C15', 'LAVES_C36', 'LAVES_C14', 'LIQUID']))==0 and p!=[] for p in gridPhasesComplete]
gridFeasibleComplete[100:125]

[True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True,
 True]

In [296]:
sum(gridFeasibleComplete)

1041

In [310]:
import pqam_rmsadtandoc2023

def c2rmsad(point):
    formula = ' '.join([f'{c}{p}' for c, p in zip(elementalSpaceComponents, point)])
    return pqam_rmsadtandoc2023.predict(formula)

In [315]:
print(compositions[0])
c2rmsad(compositions[0])

[0.0, 0.0, 0.25, 0.25, 0.25, 0.25, 0.0]


0.11816658059128823

In [318]:
avgRMSAD = sum([c2rmsad(p) for p in compositions])/len(compositions)
print(f"Average RMSAD: {avgRMSAD}")

Average RMSAD: 0.16141834794438295


In [313]:
startingNodes = [0, 1538] + random.sample(range(len(compositions)), 8)

for startingNode in startingNodes:
    print(f"Starting node ({startingNode}): {compositions[startingNode]}")

Starting node (0): [0.0, 0.0, 0.25, 0.25, 0.25, 0.25, 0.0]
Starting node (1538): [0.0, 0.0, 0.0, 0.01, 0.96, 0.0, 0.03]
Starting node (1475): [0.0, 0.18375, 0.00375, 0.0625, 0.0625, 0.0, 0.6875]
Starting node (992): [0.08333333333333333, 0.0, 0.0, 0.0075, 0.72, 0.16666666666666666, 0.0225]
Starting node (1070): [0.03125, 0.18375, 0.5975, 0.0, 0.0, 0.0, 0.1875]
Starting node (298): [0.22916666666666666, 0.1875, 0.125, 0.125, 0.125, 0.20833333333333331, 0.0]
Starting node (584): [0.5, 0.5, 0.0, 0.0, 0.0, 0.0, 0.0]
Starting node (1517): [0.0, 0.1225, 0.0025, 0.052500000000000005, 0.29, 0.0, 0.5325]
Starting node (1384): [0.0, 0.0, 0.125, 0.13, 0.605, 0.125, 0.015]
Starting node (127): [0.3666666666666667, 0.3125, 0.2375, 0.0, 0.0, 0.08333333333333333, 0.0]


In [314]:
gridFeasible = [None]*len(compositions)
queue = startingNodes.copy()
explored = set()
calcCount = 0

minRMSAD = 0.2
print(f"Minimum RMSAD: {minRMSAD}")

Minimum RMSAD: 0.2


In [319]:
while len(queue)>0:
    print(f"Queue: {queue}")
    # Skip all points with RMSAD below the minimum (inexpensive) by removing them from the queue, marking them as infeasible, and adding them to explored
    for i in queue:
        if c2rmsad(compositions[i]) < minRMSAD:
            for eq in [i] + graphNS[i]:
                gridFeasible[eq] = False
            explored = explored.union([i] + graphNS[i])
    queue = [i for i in queue if gridFeasible[i] is None]

    # Calculate CALPHAD feasibilities (expensive) of the current queue
    elPositions = [compositions[i] for i in queue]
    if len(queue)>3:
        phases = process_map(equilibrium_callable, elPositions, max_workers=4)
    else:
        phases = [equilibrium_callable(elP) for elP in elPositions]
    feasibilities = [len(set(p) & set(['LAVES_C15', 'LAVES_C36', 'LAVES_C14', 'LIQUID']))==0 and p!=[] for p in phases]

    calcCount += len(feasibilities)
    explored = explored.union(queue)

    # Create next queue based on neighbors of feasible points
    nextQueue = set()
    nextQueuePlusEquivalent = set()
    for f, i in zip(feasibilities, queue):
        # Explored point
        gridFeasible[i] = f

        # And equivalent explored points based on system stitching
        explored = explored.union(graphNS[i])
        for eq in graphNS[i]:
            gridFeasible[eq] = f

        # Expand to neighbors of the point and equivalent points (only if the node has been feasible)
        if f:
            # Node neighbors in the same subsystem
            for n in graphN[i]:
                if n not in explored and n not in nextQueuePlusEquivalent:
                    nextQueue.add(n)
                    nextQueuePlusEquivalent = nextQueuePlusEquivalent.union([n] + graphNS[n])
            # Equivalent nodes neighbors in other subsystems
            for eq in graphNS[i]:
                for n in graphN[eq]:
                    if n not in explored and n not in nextQueuePlusEquivalent:
                        nextQueue.add(n)
                        nextQueuePlusEquivalent = nextQueuePlusEquivalent.union([n] + graphNS[n])

    print(f"Calculations done: {calcCount:<5} | Explored points: {len(explored):<5}")
    queue = list(nextQueue)

Queue: [0, 1538, 1475, 992, 1070, 298, 584, 1517, 1384, 127]
Calculations done: 3     | Explored points: 25   
Queue: [128, 130, 131, 582, 583, 627, 122, 123, 126]


  0%|          | 0/9 [00:00<?, ?it/s]

Calculations done: 12    | Explored points: 41   
Queue: [129, 132, 133, 670, 672, 168, 172, 175, 176, 579, 580, 213, 217, 220, 624, 625, 116, 117, 118, 121, 124, 125]


  0%|          | 0/20 [00:00<?, ?it/s]

Calculations done: 32    | Explored points: 77   
Queue: [134, 666, 667, 669, 671, 162, 163, 167, 169, 171, 301, 174, 305, 306, 177, 436, 310, 312, 313, 441, 445, 573, 575, 448, 577, 576, 208, 212, 216, 219, 222, 618, 621, 622, 110, 109, 111, 112, 115, 119, 120]


...

Calculations done: 201   | Explored points: 428  
Queue: [803, 1060, 741, 843, 748, 798, 1106, 754, 1111, 1047, 792, 1054]


  0%|          | 0/7 [00:00<?, ?it/s]

Calculations done: 208   | Explored points: 441  
Queue: [837, 838, 742, 842, 1099, 844, 749, 1100, 1105, 793, 799]


  0%|          | 0/4 [00:00<?, ?it/s]

Calculations done: 212   | Explored points: 452  
Queue: [832, 831]
Calculations done: 212   | Explored points: 454  
